In [1]:
# import required libraries
import sys
import numpy as np
from scipy.constants import m_p, c, e
from PyHEADTAIL.particles.particles import Particles
import PyHEADTAIL.particles.generators as generators
from PyHEADTAIL.trackers.transverse_tracking import TransverseMap
from PyHEADTAIL.trackers.simple_long_tracking import RFSystems, LinearMap
import PyHEADTAIL.cobra_functions.stats as st
import matplotlib.pyplot as plt

plt.switch_backend('TkAgg')

PyHEADTAIL v1.10.5




In [2]:
# general simulation parameters
n_particles = 500
n_segments = 1

# machine parameters
circumference = 100*2*np.pi
inj_alpha_x = 0#-1.2
inj_alpha_y = 0#15
inj_beta_x = 16.#5.9 # in [m]
inj_beta_y = 16.#5.7 # in [m]
Qx = 6.25
Qy = 6.25
gamma_tr = 6.1
alpha_c_array = [gamma_tr**-2]
Vrf1_0=20e3
Vrf2_0=0
V_rf = [Vrf1_0, Vrf2_0] # in [V]
harmonic = [7, 14]
#pipe_radius = 5e-2
Bdot=0 # in T/s
bending_radius=70 # in m
phi_offset = [np.pi, 0.] #np.arcsin(bending_radius*circumference*Bdot/V_rf) # measured from aligned focussing phase (0 or pi)

# beam parameters
Ekin = 1.4e9 # in [eV]
intensity = 8e12
epsn_x = 5e-6 # in [m*rad]
epsn_y = 5e-6 # in [m*rad]
#epsn_z = 1. # 4pi*sig_z*sig_dp (*p0/e) in [eVs]

# calculations
gamma = 1 + e * Ekin / (m_p * c**2)
beta = np.sqrt(1 - gamma**-2)
print('beta: ' + str(beta))
eta = alpha_c_array[0] - gamma**-2
print('eta: ' + str(eta))
#if eta < 0:
#    phi_offset = np.pi - phi_offset
Etot = gamma * m_p * c**2 / e
p0 = np.sqrt(gamma**2 - 1) * m_p * c
Qs = np.sqrt(np.abs(eta) * V_rf[0] / (2 * np.pi * beta**2 * Etot))
print('Qs: ' + str(Qs))
beta_z = np.abs(eta) * circumference / (2 * np.pi * Qs)
print('beta_z: ' + str(beta_z))
turn_period = circumference / (beta * c)
p_increment_0= e*bending_radius*Bdot*turn_period
sigma_z_0= 100e-9/4*beta*c
print('sigma_z_0=' + str(sigma_z_0) + ' m')

# BETATRON
# Loop on number of segments and create the TransverseSegmentMap
# for each segment.
s = np.arange(0, n_segments + 1) * circumference / n_segments
alpha_x = inj_alpha_x * np.ones(n_segments)
beta_x  = inj_beta_x * np.ones(n_segments)
D_x     = np.zeros(n_segments)
alpha_y = inj_alpha_y * np.ones(n_segments)
beta_y  = inj_beta_y * np.ones(n_segments)
D_y     = np.zeros(n_segments)

# Define RF systems
rfsystems = RFSystems(circumference, harmonic, V_rf, phi_offset,
                      alpha_c_array, gamma, p_increment=p_increment_0, charge=e, mass=m_p)
rfbucket = rfsystems.get_bucket(gamma=gamma)

# Generate the particle distribution
bunch = generators.ParticleGenerator(n_particles, intensity, e, m_p, circumference, gamma, 
                        distribution_x=generators.gaussian2D(epsn_x), alpha_x=inj_alpha_x, beta_x=inj_beta_x,
                        distribution_y=generators.gaussian2D(epsn_y), alpha_y=inj_alpha_y, beta_y=inj_beta_y,
                        distribution_z=generators.RF_bucket_distribution(rfbucket, sigma_z=sigma_z_0)).generate()

beta: 0.915961008351
eta: -0.134140935078
Qs: 0.000466531765594
beta_z: 28752.7977665
sigma_z_0=6.86495505314 m
*** Maximum RMS bunch length 14.1465336956m.
... distance to target bunch length: 5.0035e-01
... distance to target bunch length: 5.0130e-01
... distance to target bunch length: -4.0770e-05
... distance to target bunch length: -1.0547e-07
... distance to target bunch length: 4.3521e-14
--> Bunch length: 6.86495505314
--> Emittance: 0.365294608096


In [3]:
# track and plot 
plt.close()
plt.ion()
fig = plt.figure(1)
ax1 = fig.add_subplot(211)
ax2 = fig.add_subplot(212)
for i in np.arange(0, 1000, 1):
    if bunch.gamma<gamma_tr:
        rfsystems.track(bunch)
        if i%100 == 0:
            bucket = rfsystems.get_bucket(gamma=bunch.gamma)
            z = np.linspace(*bucket.interval, num=100)
            dp = np.linspace(-0.02, 0.02, num=100)
            ZZ, DPP = np.meshgrid(z, dp)
            HH = bucket.hamiltonian(ZZ, DPP)
            ax1.contour(ZZ*(-harmonic[0]*2*np.pi/circumference)*180/np.pi, DPP, HH, levels=[0], colors='magenta')
            ax1.plot(bunch.z*(-harmonic[0]*2*np.pi/circumference)*180/np.pi, bunch.dp, 'o')
            #ax2.plot(i, bunch.sigma_z(), 'or')
            ax1.axis([-250, 250, -0.005,0.005])
            ax2.plot(i, bunch.gamma, 'or')
            plt.show()
            plt.pause(0.1)
            ax1.cla()
        irestart=i
#plt.ioff()

/home/juas/anaconda2/lib/python2.7/site-packages/matplotlib/backend_bases.py:2437: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)


In [4]:
# track and plot 
nbturn=1000
plt.close()
plt.ion()
fig = plt.figure(1)
ax1 = fig.add_subplot(211)
ax2 = fig.add_subplot(212)
for i in np.arange(0, nbturn, 1):
    if bunch.gamma<gamma_tr:
        if V_rf[0]>0:
            V_rf[0]=V_rf[0]-Vrf1_0/nbturn
            V_rf[1]=V_rf[1]+4*Vrf1_0/nbturn
        rfsystems = RFSystems(circumference, harmonic, V_rf, phi_offset,
                      alpha_c_array, gamma, p_increment=p_increment_0, charge=e, mass=m_p)
        rfsystems.track(bunch)
        if i%10 == 0:
            bucket = rfsystems.get_bucket(gamma=bunch.gamma)
            z = np.linspace(*bucket.interval, num=100)
            dp = np.linspace(-0.02, 0.02, num=100)
            ZZ, DPP = np.meshgrid(z, dp)
            HH = bucket.hamiltonian(ZZ, DPP)
            ax1.contour(ZZ*(-harmonic[0]*2*np.pi/circumference)*180/np.pi, DPP, HH, levels=[0], colors='magenta')
            ax1.plot(bunch.z*(-harmonic[0]*2*np.pi/circumference)*180/np.pi, bunch.dp, 'o')
            #ax2.plot(i, bunch.sigma_z(), 'or')
            ax1.axis([-250, 250, -0.005,0.005])
            ax2.plot(i, V_rf[1], 'or')
            plt.show()
            plt.pause(0.1)
            ax1.cla()
            #print V_rf
        irestart=i
#plt.ioff()

In [ ]:
V_rf=[0,20e3]

In [ ]:
rfsystems = RFSystems(circumference, harmonic, V_rf, phi_offset,
                      alpha_c_array, gamma, p_increment=p_increment_0, charge=e, mass=m_p)
rfbucket = rfsystems.get_bucket(gamma=gamma)

In [ ]:
V_rf[0]=20-i*

In [ ]:
V_rf